In [2]:
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


# Accessing through my Drive

In [7]:
%cd /content/gdrive/MyDrive/Thesis_work/POINTNET/ModelNet30

/content/gdrive/MyDrive/Thesis_work/POINTNET/ModelNet30


# Accessing Through Vai Drive

In [ ]:
%cd /content/gdrive/MyDrive/Thesis_work/POINTNET

/content/gdrive/MyDrive/Thesis_work/POINTNET


In [4]:
import numpy as np
import math
import random
import os
import torch
import pandas as pd
import scipy.spatial.distance
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms, utils

import plotly.graph_objects as go
import plotly.express as px

In [5]:
!pip install path.py;
from path import Path

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [8]:
random.seed = 49
path = Path("/content/gdrive/MyDrive/Thesis_work/POINTNET/ModelNet30")
print(path)

/content/gdrive/MyDrive/Thesis_work/POINTNET/ModelNet30


In [9]:
folders = [dir for dir in sorted(os.listdir(path)) if os.path.isdir(path/dir)]
classes = {folder: i for i, folder in enumerate(folders)};
classes

{'airplane': 0,
 'bench': 1,
 'bookshelf': 2,
 'bottle': 3,
 'bowl': 4,
 'car': 5,
 'cone': 6,
 'cup': 7,
 'curtain': 8,
 'door': 9,
 'flower_pot': 10,
 'glass_box': 11,
 'guitar': 12,
 'keyboard': 13,
 'lamp': 14,
 'laptop': 15,
 'mantel': 16,
 'person': 17,
 'piano': 18,
 'plant': 19,
 'radio': 20,
 'range_hood': 21,
 'sink': 22,
 'stairs': 23,
 'stool': 24,
 'tent': 25,
 'tv_stand': 26,
 'vase': 27,
 'wardrobe': 28,
 'xbox': 29}

In [10]:
def read_off(file):
    first_line = file.readline()
    if len(first_line) != 4:
        #first_line = first_line.decode("utf-8")
        #print(type(first_line))
        #print(first_line)
        line = first_line.strip('OFF').split()
        n_verts, n_faces, __ = tuple([int(s) for s in line])
    else:
        n_verts, n_faces, __ = tuple([int(s) for s in file.readline().strip().split(' ')])
    # if 'OFF' != file.readline().strip():
    #     raise('Not a valid OFF header')
    
    verts = [[float(s) for s in file.readline().strip().split(' ')] for i_vert in range(n_verts)]
    faces = [[int(s) for s in file.readline().strip().split(' ')][1:] for i_face in range(n_faces)]
    return verts, faces

In [29]:
with open("/content/gdrive/MyDrive/Thesis_work/POINTNET/ModelNet30/airplane/train/airplane_0003.off", 'r') as f:
  verts, faces = read_off(f)

In [30]:
i,j,k = np.array(faces).T
x,y,z = np.array(verts).T

## Visualization


In [31]:
def visualize_rotate(data):
    x_eye, y_eye, z_eye = 1.25, 1.25, 0.8
    frames=[]

    def rotate_z(x, y, z, theta):
        w = x+1j*y
        return np.real(np.exp(1j*theta)*w), np.imag(np.exp(1j*theta)*w), z

    for t in np.arange(0, 10.26, 0.1):
        xe, ye, ze = rotate_z(x_eye, y_eye, z_eye, -t)
        frames.append(dict(layout=dict(scene=dict(camera=dict(eye=dict(x=xe, y=ye, z=ze))))))
    fig = go.Figure(data=data,
                    layout=go.Layout(
                        updatemenus=[dict(type='buttons',
                                    showactive=False,
                                    y=1,
                                    x=0.8,
                                    xanchor='left',
                                    yanchor='bottom',
                                    pad=dict(t=45, r=10),
                                    buttons=[dict(label='Play',
                                                    method='animate',
                                                    args=[None, dict(frame=dict(duration=50, redraw=True),
                                                                    transition=dict(duration=0),
                                                                    fromcurrent=True,
                                                                    mode='immediate'
                                                                    )]
                                                    )
                                            ]
                                    )
                                ]
                    ),
                    frames=frames
            )

    return fig

In [32]:
visualize_rotate([go.Mesh3d(x=x, y=y, z=z, color='lightpink', opacity=0.50, i=i,j=j,k=k)]).show()

In [33]:
visualize_rotate([go.Scatter3d(x=x, y=y, z=z,
                                   mode='markers')]).show()

In [27]:
def pcshow(xs,ys,zs):
    data=[go.Scatter3d(x=xs, y=ys, z=zs,
                                   mode='markers')]
    fig = visualize_rotate(data)
    fig.update_traces(marker=dict(size=2,
                      line=dict(width=2,
                      color='DarkSlateGrey')),
                      selector=dict(mode='markers'))
    fig.show()

In [34]:
pcshow(x,y,z)

# Transform
## Sample points

In [ ]:
class PointSampler(object):
    def __init__(self, output_size):
        assert isinstance(output_size, int)
        self.output_size = output_size
    
    def triangle_area(self, pt1, pt2, pt3):
        side_a = np.linalg.norm(pt1 - pt2)
        side_b = np.linalg.norm(pt2 - pt3)
        side_c = np.linalg.norm(pt3 - pt1)
        s = 0.5 * ( side_a + side_b + side_c)
        return max(s * (s - side_a) * (s - side_b) * (s - side_c), 0)**0.5

    def sample_point(self, pt1, pt2, pt3):
        # barycentric coordinates on a triangle
        # https://mathworld.wolfram.com/BarycentricCoordinates.html
        s, t = sorted([random.random(), random.random()])
        f = lambda i: s * pt1[i] + (t-s)*pt2[i] + (1-t)*pt3[i]
        return (f(0), f(1), f(2))
        
    
    def __call__(self, mesh):
        verts, faces = mesh
        verts = np.array(verts)
        areas = np.zeros((len(faces)))

        for i in range(len(areas)):
            areas[i] = (self.triangle_area(verts[faces[i][0]],
                                           verts[faces[i][1]],
                                           verts[faces[i][2]]))
            
        sampled_faces = (random.choices(faces, 
                                      weights=areas,
                                      cum_weights=None,
                                      k=self.output_size))
        
        sampled_points = np.zeros((self.output_size, 3))

        for i in range(len(sampled_faces)):
            sampled_points[i] = (self.sample_point(verts[sampled_faces[i][0]],
                                                   verts[sampled_faces[i][1]],
                                                   verts[sampled_faces[i][2]]))
        
        return sampled_points

In [ ]:
pointcloud = PointSampler(3000)((verts, faces))

In [ ]:
pcshow(*pointcloud.T)

NameError: ignored

# Normalize

In [ ]:
class Normalize(object):
    def __call__(self, pointcloud):
        assert len(pointcloud.shape)==2
        
        norm_pointcloud = pointcloud - np.mean(pointcloud, axis=0) 
        norm_pointcloud /= np.max(np.linalg.norm(norm_pointcloud, axis=1))

        return  norm_pointcloud

In [ ]:
norm_pointcloud = Normalize()(pointcloud) 

In [ ]:
pcshow(*norm_pointcloud.T)

# Augmentations
## Add random rotations

In [ ]:
class RandRotation_z(object):
    def __call__(self, pointcloud):
        assert len(pointcloud.shape)==2

        theta = random.random() * 2. * math.pi
        rot_matrix = np.array([[ math.cos(theta), -math.sin(theta),    0],
                               [ math.sin(theta),  math.cos(theta),    0],
                               [0,                             0,      1]])
        
        rot_pointcloud = rot_matrix.dot(pointcloud.T).T
        return  rot_pointcloud
    
class RandomNoise(object):
    def __call__(self, pointcloud):
        assert len(pointcloud.shape)==2

        noise = np.random.normal(0, 0.02, (pointcloud.shape))
    
        noisy_pointcloud = pointcloud + noise
        return  noisy_pointcloud

In [ ]:
rot_pointcloud = RandRotation_z()(norm_pointcloud)
noisy_rot_pointcloud = RandomNoise()(rot_pointcloud)

In [ ]:
pcshow(*noisy_rot_pointcloud.T)

# To Tensor

In [ ]:
class ToTensor(object):
    def __call__(self, pointcloud):
        assert len(pointcloud.shape)==2

        return torch.from_numpy(pointcloud)

In [ ]:
ToTensor()(noisy_rot_pointcloud)

tensor([[-0.0856,  0.8048, -0.2168],
        [ 0.0682, -0.8448,  0.0039],
        [ 0.1075, -0.7173,  0.0475],
        ...,
        [-0.1920,  0.0135,  0.0268],
        [ 0.1107,  0.0327, -0.0387],
        [-0.0234, -0.8357, -0.0260]], dtype=torch.float64)

In [ ]:
def default_transforms():
    return transforms.Compose([
                                PointSampler(1024),
                                Normalize(),
                                ToTensor()
                              ])

# Custom Dataset

In [ ]:
class PointCloudData(Dataset):
    def __init__(self, root_dir, valid=False, folder="train", transform=default_transforms()):
        self.root_dir = root_dir
        folders = [dir for dir in sorted(os.listdir(root_dir)) if os.path.isdir(root_dir/dir)]
        self.classes = {folder: i for i, folder in enumerate(folders)}
        self.transforms = transform if not valid else default_transforms()
        self.valid = valid
        self.files = []
        for category in self.classes.keys():
            new_dir = root_dir/Path(category)/folder
            for file in os.listdir(new_dir):
                if file.endswith('.off'):
                    sample = {}
                    sample['pcd_path'] = new_dir/file
                    sample['category'] = category
                    self.files.append(sample)

    def __len__(self):
        return len(self.files)

    def __preproc__(self, file):
        verts, faces = read_off(file)
        if self.transforms:
            pointcloud = self.transforms((verts, faces))
        return pointcloud

    def __getitem__(self, idx):
        pcd_path = self.files[idx]['pcd_path']
        category = self.files[idx]['category']
        with open(pcd_path, 'r') as f:
            pointcloud = self.__preproc__(f)
        return {'pointcloud': pointcloud, 
                'category': self.classes[category]}

In [ ]:
train_transforms = transforms.Compose([
                    PointSampler(1024),
                    Normalize(),
                    RandRotation_z(),
                    RandomNoise(),
                    ToTensor()
                    ])

In [ ]:
train_ds = PointCloudData(path, transform=train_transforms)
valid_ds = PointCloudData(path, valid=True, folder='test', transform=train_transforms)

In [ ]:
inv_classes = {i: cat for cat, i in train_ds.classes.items()};
inv_classes

{0: 'airplane',
 1: 'bench',
 2: 'bookshelf',
 3: 'bottle',
 4: 'bowl',
 5: 'car',
 6: 'cone',
 7: 'cup',
 8: 'curtain',
 9: 'door',
 10: 'flower_pot',
 11: 'glass_box',
 12: 'guitar',
 13: 'keyboard',
 14: 'lamp',
 15: 'laptop',
 16: 'mantel',
 17: 'person',
 18: 'piano',
 19: 'plant',
 20: 'radio',
 21: 'range_hood',
 22: 'sink',
 23: 'stairs',
 24: 'stool',
 25: 'tent',
 26: 'tv_stand',
 27: 'vase',
 28: 'wardrobe',
 29: 'xbox'}

In [ ]:
print('Train dataset size: ', len(train_ds))
print('Valid dataset size: ', len(valid_ds))
print('Number of classes: ', len(train_ds.classes))
print('Sample pointcloud shape: ', train_ds[0]['pointcloud'].size())
print('Class: ', inv_classes[train_ds[0]['category']])

Train dataset size:  5852
Valid dataset size:  1560
Number of classes:  30
Sample pointcloud shape:  torch.Size([1024, 3])
Class:  airplane


In [ ]:
train_loader = DataLoader(dataset=train_ds, batch_size=32, shuffle=True)
valid_loader = DataLoader(dataset=valid_ds, batch_size=64)

# Model

In [ ]:
import torch
import torch.nn as nn
import numpy as np
import torch.nn.functional as F

class Tnet(nn.Module):
   def __init__(self, k=3):
      super().__init__()
      self.k=k
      self.conv1 = nn.Conv1d(k,64,1)
      self.conv2 = nn.Conv1d(64,128,1)
      self.conv3 = nn.Conv1d(128,1024,1)
      self.fc1 = nn.Linear(1024,512)
      self.fc2 = nn.Linear(512,256)
      self.fc3 = nn.Linear(256,k*k)

      self.bn1 = nn.BatchNorm1d(64)
      self.bn2 = nn.BatchNorm1d(128)
      self.bn3 = nn.BatchNorm1d(1024)
      self.bn4 = nn.BatchNorm1d(512)
      self.bn5 = nn.BatchNorm1d(256)
       

   def forward(self, input):
      # input.shape == (bs,n,3)
      bs = input.size(0)
      xb = F.relu(self.bn1(self.conv1(input)))
      xb = F.relu(self.bn2(self.conv2(xb)))
      xb = F.relu(self.bn3(self.conv3(xb)))
      pool = nn.MaxPool1d(xb.size(-1))(xb)
      flat = nn.Flatten(1)(pool)
      xb = F.relu(self.bn4(self.fc1(flat)))
      xb = F.relu(self.bn5(self.fc2(xb)))
      
      #initialize as identity
      init = torch.eye(self.k, requires_grad=True).repeat(bs,1,1)
      if xb.is_cuda:
        init=init.cuda()
      matrix = self.fc3(xb).view(-1,self.k,self.k) + init
      return matrix


class Transform(nn.Module):
   def __init__(self):
        super().__init__()
        self.input_transform = Tnet(k=3)
        self.feature_transform = Tnet(k=64)
        self.conv1 = nn.Conv1d(3,64,1)

        self.conv2 = nn.Conv1d(64,128,1)
        self.conv3 = nn.Conv1d(128,1024,1)

        self.bn1 = nn.BatchNorm1d(64)
        self.bn2 = nn.BatchNorm1d(128)
        self.bn3 = nn.BatchNorm1d(1024)

        self.tanh = nn.Tanh()
        #self.softMax = nn.Softmax(dim=1)
       
   def forward(self, input):
        matrix3x3 = self.input_transform(input)
        # batch matrix multiplication
        xb = torch.bmm(torch.transpose(input,1,2), matrix3x3).transpose(1,2)

        xb = F.relu(self.bn1(self.conv1(xb)))

        matrix64x64 = self.feature_transform(xb)
        xb = torch.bmm(torch.transpose(xb,1,2), matrix64x64).transpose(1,2)

        xb = F.relu(self.bn2(self.conv2(xb)))
        xb = self.bn3(self.conv3(xb))
        xb = nn.MaxPool1d(xb.size(-1))(xb)
        output = nn.Flatten(1)(xb)
        return self.tanh(output), matrix3x3, matrix64x64

class PointNet(nn.Module):
    def __init__(self, classes = 30):
        super().__init__()
        self.transform = Transform()
        self.fc1 = nn.Linear(1024, 512)
        self.fc2 = nn.Linear(512, 256)
        self.fc3 = nn.Linear(256, classes)
        

        self.bn1 = nn.BatchNorm1d(512)
        self.bn2 = nn.BatchNorm1d(256)
        self.dropout = nn.Dropout(p=0.3)
        self.logsoftmax = nn.LogSoftmax(dim=1)

    def forward(self, input):
        xb, matrix3x3, matrix64x64 = self.transform(input)
        xb = F.relu(self.bn1(self.fc1(xb)))
        xb = F.relu(self.bn2(self.dropout(self.fc2(xb))))
        output = self.fc3(xb)
        return self.logsoftmax(output), matrix3x3, matrix64x64

In [ ]:
def pointnetloss(outputs, labels, m3x3, m64x64, alpha = 0.0001):
    criterion = torch.nn.NLLLoss()
    bs=outputs.size(0)
    id3x3 = torch.eye(3, requires_grad=True).repeat(bs,1,1)
    id64x64 = torch.eye(64, requires_grad=True).repeat(bs,1,1)
    if outputs.is_cuda:
        id3x3=id3x3.cuda()
        id64x64=id64x64.cuda()
    diff3x3 = id3x3-torch.bmm(m3x3,m3x3.transpose(1,2))
    diff64x64 = id64x64-torch.bmm(m64x64,m64x64.transpose(1,2))
    return criterion(outputs, labels) + alpha * (torch.norm(diff3x3)+torch.norm(diff64x64)) / float(bs)

# Training loop

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
print(device)

cuda:0


In [ ]:
model = PointNet()
model.to(device)

PointNet(
  (transform): Transform(
    (input_transform): Tnet(
      (conv1): Conv1d(3, 64, kernel_size=(1,), stride=(1,))
      (conv2): Conv1d(64, 128, kernel_size=(1,), stride=(1,))
      (conv3): Conv1d(128, 1024, kernel_size=(1,), stride=(1,))
      (fc1): Linear(in_features=1024, out_features=512, bias=True)
      (fc2): Linear(in_features=512, out_features=256, bias=True)
      (fc3): Linear(in_features=256, out_features=9, bias=True)
      (bn1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (bn2): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (bn3): BatchNorm1d(1024, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (bn4): BatchNorm1d(512, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (bn5): BatchNorm1d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (feature_transform): Tnet(
      (conv1): Conv1d(64, 64, kernel_size=(1,

In [ ]:
optimizer = torch.optim.Adam(model.parameters(), lr=0.0001)

In [ ]:
PATH = "/content/gdrive/MyDrive/Thesis_work/POINTNET/new_31_85.pth"

In [ ]:
checkpoint = torch.load(PATH)
model.load_state_dict(checkpoint['model_state_dict'])
optimizer.load_state_dict(checkpoint['optimizer_state_dict'])
epoch = checkpoint['epoch']
loss = checkpoint['loss']

In [ ]:
def train(model, train_loader, val_loader=None,  epochs=15, save=True):
    for epoch in range(epochs): 
        model.train()
        running_loss = 0.0
        for i, data in enumerate(train_loader, 0):
            inputs, labels = data['pointcloud'].to(device).float(), data['category'].to(device)
            optimizer.zero_grad()
            outputs, m3x3, m64x64 = model(inputs.transpose(1,2))

            loss = pointnetloss(outputs, labels, m3x3, m64x64)
            loss.backward()
            optimizer.step()

            # print statistics
            running_loss += loss.item()
            if i % 10 == 9:    # print every 10 mini-batches
                    print('[Epoch: %d, Batch: %4d / %4d], loss: %.3f' %
                        (epoch + 1, i + 1, len(train_loader), running_loss / 10))
                    running_loss = 0.0
        # save the model
        if save:
          torch.save({
            'epoch': epoch,
            'model_state_dict': model.state_dict(),
            'optimizer_state_dict': optimizer.state_dict(),
            'loss': loss,
            }, "tanh_"+str(epoch+15)+".pth")

        model.eval()
        correct = total = 0

        if val_loader:
            with torch.no_grad():
                for data in val_loader:
                    inputs, labels = data['pointcloud'].to(device).float(), data['category'].to(device)
                    outputs, __, __ = model(inputs.transpose(1,2))
                    _, predicted = torch.max(outputs.data, 1)
                    total += labels.size(0)
                    correct += (predicted == labels).sum().item()
            val_acc = 100. * correct / total
            print('Valid accuracy: %f %%' % val_acc)

        
          #torch.save(pointnet.state_dict(), "save_"+str(epoch)+".pth")

In [ ]:
train(model, train_loader, valid_loader,  save=True)

[Epoch: 1, Batch:   10 /  183], loss: 0.673
[Epoch: 1, Batch:   20 /  183], loss: 0.739
[Epoch: 1, Batch:   30 /  183], loss: 0.669
[Epoch: 1, Batch:   40 /  183], loss: 0.728
[Epoch: 1, Batch:   50 /  183], loss: 0.693
[Epoch: 1, Batch:   60 /  183], loss: 0.620
[Epoch: 1, Batch:   70 /  183], loss: 0.722
[Epoch: 1, Batch:   80 /  183], loss: 0.582
[Epoch: 1, Batch:   90 /  183], loss: 0.575
[Epoch: 1, Batch:  100 /  183], loss: 0.628
[Epoch: 1, Batch:  110 /  183], loss: 0.627
[Epoch: 1, Batch:  120 /  183], loss: 0.563
[Epoch: 1, Batch:  130 /  183], loss: 0.691
[Epoch: 1, Batch:  140 /  183], loss: 0.658
[Epoch: 1, Batch:  150 /  183], loss: 0.744
[Epoch: 1, Batch:  160 /  183], loss: 0.600
[Epoch: 1, Batch:  170 /  183], loss: 0.649
[Epoch: 1, Batch:  180 /  183], loss: 0.667
Valid accuracy: 79.551282 %
[Epoch: 2, Batch:   10 /  183], loss: 0.553
[Epoch: 2, Batch:   20 /  183], loss: 0.595
[Epoch: 2, Batch:   30 /  183], loss: 0.622
[Epoch: 2, Batch:   40 /  183], loss: 0.607
[Epo

# Validation Check

In [ ]:
model.eval()
correct = total = 0
with torch.no_grad():
   for i, data in enumerate(valid_loader):
       inputs, labels = data['pointcloud'].to(device).float(), data['category'].to(device)
       outputs, __, __ = model(inputs.transpose(1,2))
       _, predicted = torch.max(outputs.data, 1)
       total += labels.size(0)
       correct += (predicted == labels).sum().item()
       if i % 5 == 0:    # print every 10 mini-batches
                    print('[Epoch: %d, Batch: %4d / %4d]' %
                        (epoch + 1, i + 1, len(valid_loader)))
val_acc = 100. * correct / total
print('Valid accuracy: %d %%' % val_acc)

[Epoch: 4, Batch:    1 /   25]
[Epoch: 4, Batch:    6 /   25]
[Epoch: 4, Batch:   11 /   25]
[Epoch: 4, Batch:   16 /   25]
[Epoch: 4, Batch:   21 /   25]
Valid accuracy: 77 %


# Extracting Feature Vector

## Redefine Model

In [ ]:
import torch
import torch.nn as nn
import numpy as np
import torch.nn.functional as F

class Tnet(nn.Module):
   def __init__(self, k=3):
      super().__init__()
      self.k=k
      self.conv1 = nn.Conv1d(k,64,1)
      self.conv2 = nn.Conv1d(64,128,1)
      self.conv3 = nn.Conv1d(128,1024,1)
      self.fc1 = nn.Linear(1024,512)
      self.fc2 = nn.Linear(512,256)
      self.fc3 = nn.Linear(256,k*k)

      self.bn1 = nn.BatchNorm1d(64)
      self.bn2 = nn.BatchNorm1d(128)
      self.bn3 = nn.BatchNorm1d(1024)
      self.bn4 = nn.BatchNorm1d(512)
      self.bn5 = nn.BatchNorm1d(256)
       

   def forward(self, input):
      # input.shape == (bs,n,3)
      bs = input.size(0)
      xb = F.relu(self.bn1(self.conv1(input)))
      xb = F.relu(self.bn2(self.conv2(xb)))
      xb = F.relu(self.bn3(self.conv3(xb)))
      pool = nn.MaxPool1d(xb.size(-1))(xb)
      flat = nn.Flatten(1)(pool)
      xb = F.relu(self.bn4(self.fc1(flat)))
      xb = F.relu(self.bn5(self.fc2(xb)))
      
      #initialize as identity
      init = torch.eye(self.k, requires_grad=True).repeat(bs,1,1)
      if xb.is_cuda:
        init=init.cuda()
      matrix = self.fc3(xb).view(-1,self.k,self.k) + init
      return matrix


class Transform(nn.Module):
   def __init__(self):
        super().__init__()
        self.input_transform = Tnet(k=3)
        self.feature_transform = Tnet(k=64)
        self.conv1 = nn.Conv1d(3,64,1)

        self.conv2 = nn.Conv1d(64,128,1)
        self.conv3 = nn.Conv1d(128,1024,1)

        self.bn1 = nn.BatchNorm1d(64)
        self.bn2 = nn.BatchNorm1d(128)
        self.bn3 = nn.BatchNorm1d(1024)

        self.tanh = nn.Tanh()
        #self.softMax = nn.Softmax(dim=1)
       
   def forward(self, input):
        matrix3x3 = self.input_transform(input)
        # batch matrix multiplication
        xb = torch.bmm(torch.transpose(input,1,2), matrix3x3).transpose(1,2)

        xb = F.relu(self.bn1(self.conv1(xb)))

        matrix64x64 = self.feature_transform(xb)
        xb = torch.bmm(torch.transpose(xb,1,2), matrix64x64).transpose(1,2)

        xb = F.relu(self.bn2(self.conv2(xb)))
        xb = self.bn3(self.conv3(xb))
        xb = nn.MaxPool1d(xb.size(-1))(xb)
        output = nn.Flatten(1)(xb)
        return self.tanh(output), matrix3x3, matrix64x64

class PointNet(nn.Module):
    def __init__(self, classes = 30):
        super().__init__()
        self.transform = Transform()
        self.fc1 = nn.Linear(1024, 512)
        self.fc2 = nn.Linear(512, 256)
        self.fc3 = nn.Linear(256, classes)
        

        self.bn1 = nn.BatchNorm1d(512)
        self.bn2 = nn.BatchNorm1d(256)
        self.dropout = nn.Dropout(p=0.3)
        self.logsoftmax = nn.LogSoftmax(dim=1)

    def forward(self, input):
        xb1, matrix3x3, matrix64x64 = self.transform(input)
        xb = F.relu(self.bn1(self.fc1(xb1)))
        xb = F.relu(self.bn2(self.dropout(self.fc2(xb))))
        output = self.fc3(xb)
        return xb1, self.logsoftmax(output), matrix3x3, matrix64x64

## Dataset 

In [ ]:
Path("/content/gdrive/MyDrive/Thesis_work/POINTNET/Medical_object")

Path('/content/gdrive/MyDrive/Thesis_work/POINTNET/Medical_object')

In [ ]:
train_ds = PointCloudData(path, folder='test', transform=train_transforms)

In [ ]:
inv_classes = {i: cat for cat, i in train_ds.classes.items()}
inv_classes

{0: 'Cart',
 1: 'Forceps',
 2: 'Hospital_bed',
 3: 'Scoope',
 4: 'Stethoscop',
 5: 'Syringe',
 6: 'WheelChair'}

In [ ]:
print('Train dataset size: ', len(train_ds))
print('Number of classes: ', len(train_ds.classes))

Train dataset size:  29
Number of classes:  7


In [ ]:
train_loader = DataLoader(dataset=train_ds, shuffle=False)

In [ ]:
for i, data in enumerate(train_loader, 0):
  print(data)

{'pointcloud': tensor([[[-0.0205, -0.3540,  0.2391],
         [-0.2015, -0.3366,  0.2571],
         [-0.1637,  0.2037, -0.6679],
         ...,
         [ 0.4015, -0.5607, -0.3853],
         [-0.3139,  0.3115,  0.2360],
         [ 0.2956, -0.5398,  0.0442]]], dtype=torch.float64), 'category': tensor([0])}
{'pointcloud': tensor([[[ 0.2838,  0.1429,  0.3236],
         [ 0.0936,  0.0879, -0.3566],
         [-0.4937,  0.7140, -0.1530],
         ...,
         [-0.1095, -0.3290,  0.3269],
         [-0.2077, -0.0598,  0.2911],
         [ 0.1741, -0.5423,  0.2819]]], dtype=torch.float64), 'category': tensor([0])}
{'pointcloud': tensor([[[-0.1517, -0.2513, -0.0101],
         [ 0.0238,  0.6096, -0.1948],
         [ 0.1448, -0.3037, -0.3111],
         ...,
         [-0.0058,  0.5113, -0.0263],
         [-0.2998, -0.5881,  0.1222],
         [-0.1351, -0.4904,  0.1124]]], dtype=torch.float64), 'category': tensor([0])}
{'pointcloud': tensor([[[ 0.0682,  0.6650,  0.3033],
         [-0.5435,  0.3848,  

KeyboardInterrupt: ignored

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
print(device)

cuda:0


In [ ]:
model = PointNet()
model.to(device)

PointNet(
  (transform): Transform(
    (input_transform): Tnet(
      (conv1): Conv1d(3, 64, kernel_size=(1,), stride=(1,))
      (conv2): Conv1d(64, 128, kernel_size=(1,), stride=(1,))
      (conv3): Conv1d(128, 1024, kernel_size=(1,), stride=(1,))
      (fc1): Linear(in_features=1024, out_features=512, bias=True)
      (fc2): Linear(in_features=512, out_features=256, bias=True)
      (fc3): Linear(in_features=256, out_features=9, bias=True)
      (bn1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (bn2): BatchNorm1d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (bn3): BatchNorm1d(1024, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (bn4): BatchNorm1d(512, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (bn5): BatchNorm1d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (feature_transform): Tnet(
      (conv1): Conv1d(64, 64, kernel_size=(1,

In [ ]:
PATH = "/content/gdrive/MyDrive/Thesis_work/POINTNET/new_31_85.pth"

In [ ]:
checkpoint = torch.load(PATH)
model.load_state_dict(checkpoint['model_state_dict'])

<All keys matched successfully>

In [ ]:
def feedforward(train_loader):
    model.eval()
    df = pd.DataFrame(columns=[i for i in range(1025)])
    #feature_vector = torch.zeros([1, 1024], dtype=torch.int32).to(device) 
    for i, data in enumerate(train_loader, 0):
        inputs, labels = data['pointcloud'].to(device).float(), data['category'].to(device)
        feature_vector, outputs, m3x3, m64x64 = model(inputs.transpose(1,2))
        feature_vector_np = feature_vector.cpu().detach().numpy()
        label_np = labels.cpu().detach().numpy()
        # print(len(label_np), feature_vector_np.shape)
        # print(df.shape)
        df.loc[i] = np.append(label_np, feature_vector_np.flatten())
        #feature_vector = torch.cat((feature_vector, vector), dim=0)
        if i % 100 == 0:
            print(f"DataFrame Size {df.shape}")
            print(df.head(i))
    df.to_csv('/content/gdrive/MyDrive/Thesis_work/POINTNET/csv_tanh/feature_vector_medical_object_test.csv')
    print("Done")

In [ ]:
feedforward(train_loader)

DataFrame Size (1, 1025)
Empty DataFrame
Columns: [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, ...]
Index: []

[0 rows x 1025 columns]
Done


# Converting CSV to PKL

In [ ]:
import pandas as pd
import numpy as np
import pickle

In [ ]:
df = pd.read_csv("/gdrive/MyDrive/PointNet/final_feature_vector_test_model30.csv")
df.head()

Unnamed: 0    0         1         2  ...      1021      1022      1023      1024
0           0  0.0  0.000249  0.000152  ...  0.000122  0.000076  0.000113  0.000874
1           1  0.0  0.000441  0.000223  ...  0.000239  0.000238  0.000121  0.001271
2           2  0.0  0.000295  0.000264  ...  0.000413  0.000094  0.000175  0.001696
3           3  0.0  0.000443  0.000320  ...  0.000323  0.000155  0.000220  0.001341
4           4  0.0  0.001167  0.000150  ...  0.000264  0.000139  0.000211  0.002006

[5 rows x 1026 columns]

In [ ]:
df.drop(df.columns[[0]], axis=1, inplace=True)

In [ ]:
df.head()

0         1         2         3  ...      1021      1022      1023      1024
0  0.0  0.000249  0.000152  0.000336  ...  0.000122  0.000076  0.000113  0.000874
1  0.0  0.000441  0.000223  0.000210  ...  0.000239  0.000238  0.000121  0.001271
2  0.0  0.000295  0.000264  0.000417  ...  0.000413  0.000094  0.000175  0.001696
3  0.0  0.000443  0.000320  0.000433  ...  0.000323  0.000155  0.000220  0.001341
4  0.0  0.001167  0.000150  0.000496  ...  0.000264  0.000139  0.000211  0.002006

[5 rows x 1025 columns]

In [ ]:
pkl_file = open("feature_vector_test_model30.pkl", "wb")
pickle.dump(df, pkl_file)

# Mat File save

In [ ]:
import pandas as pd
df_train = pd.read_csv('/content/gdrive/MyDrive/Thesis_work/POINTNET/csv_tanh/feature_vector_train_model30.csv')

In [ ]:
df_train.drop(df_train.columns[[0]], axis=1, inplace=True)

In [ ]:
df_train

1         2         3  ...      1022      1023      1024
0     0.444914  0.935517  0.764654  ...  0.767211  0.697334  0.173836
1     0.358353  0.837690  0.750746  ...  0.904189  0.538422  0.641538
2     0.425052  0.995242  0.619234  ...  0.800704  0.858724  0.282496
3     0.519823  0.994885  0.824918  ...  0.924401  0.905928  0.472035
4     0.491916  0.946885  0.767002  ...  0.854044  0.899577  0.125993
...        ...       ...       ...  ...       ...       ...       ...
5847  0.992632  0.998147  0.070231  ...  0.820245  0.958198  0.866989
5848  0.974062  0.993152  0.085875  ...  0.863449  0.929388  0.843384
5849  0.981461  0.984158  0.212667  ...  0.766845  0.976130  0.747829
5850  0.979981  0.993120  0.919318  ...  0.614505  0.990049  0.886930
5851  0.999694  0.999637  0.274075  ...  0.931213  0.939303  0.891899

[5852 rows x 1024 columns]

In [ ]:
df_numpy = df_train.to_numpy()

In [ ]:
df_numpy.shape

(5852, 1024)

In [ ]:
mat = {'pfc_feat': df_numpy}

In [ ]:
from scipy.io import savemat, loadmat
savemat("/content/gdrive/MyDrive/Thesis_work/Mat_File/feature_vector_train_model30.mat", mat)

In [ ]:
GAN = loadmat('/content/gdrive/MyDrive/Thesis_work/Mat_File/feature_vector_train_model30.mat')

In [ ]:
np_ar = GAN['pfc_feat']

In [ ]:
np_ar.shape

(5852, 1024)

# Preparating Data

# Read Mat File

In [ ]:
import scipy.io as sio
GAN = sio.loadmat('/content/gdrive/MyDrive/Thesis_work/zhu_ZSL_GAN/ZSL_GAN/GAN_FEATURES_MODELNET_UTTANH(300)_RESNET.mat')

In [ ]:
GAN['gan_feat']

array([[ 0.99998432,  1.        , -0.99911356, ...,  1.        ,
         0.73939836, -0.96651244],
       [-0.99993241, -0.98130351, -0.99999821, ..., -0.99918205,
         0.99916828, -0.99956632],
       [ 0.50844836, -0.92679507, -1.        , ...,  0.84612918,
        -1.        ,  0.43212667],
       ...,
       [-0.9980135 ,  0.9999544 , -0.94456822, ...,  0.73853409,
         0.9989295 , -0.99999815],
       [-0.67886555,  1.        , -0.94820464, ...,  0.94029409,
        -0.4523569 ,  0.6643244 ],
       [ 0.81394619,  0.99999911,  1.        , ...,  0.9998368 ,
         1.        , -0.9682067 ]])

# CSV file read


In [ ]:
df_numpy = np.delete(np_ar, 0, 1)

In [ ]:
df_numpy.shape

(908, 1024)

In [ ]:
import pandas as pd
#df_GAN = pd.read_csv('/gdrive/MyDrive/Thesis_work/POINTNET/GAN_feature_200.csv', sep=',',header=None)
df_train = pd.read_csv('/content/gdrive/MyDrive/Thesis_work/POINTNET/csv_tanh/feature_vector_train_model30.csv')
df_test1 = pd.read_csv('/content/gdrive/MyDrive/Thesis_work/POINTNET/csv_tanh/feature_vector_test_model10.csv')
#df_test2 = pd.read_csv('/content/gdrive/MyDrive/Thesis_work/POINTNET/csv_tanh/feature_vector_test_model30.csv')

In [ ]:
df_test2.shape
#df_test1.head()

(1560, 1026)

In [ ]:
import numpy as np

def sigmoid(x):
  return 1 / (1 + np.exp(-x))

## Prepararing Data for train data 5852

In [ ]:
df_train.drop(df_train.columns[[0]], axis=1, inplace=True)
label = df_train['0']
labels = label.to_numpy()
labels = labels.astype(np.int32)
df_train.drop(df_train.columns[[0]], axis=1, inplace=True)
feature = df_train.to_numpy()
feature = sigmoid(feature)
print(feature, labels)

[[0.60942924 0.71819329 0.68236332 ... 0.6829172  0.66759643 0.54335   ]
 [0.58864179 0.69797853 0.6793412  ... 0.71180958 0.63144528 0.65510105]
 [0.60469153 0.73012212 0.65004436 ... 0.690125   0.70239404 0.57015798]
 ...
 [0.72739804 0.72793247 0.5529672  ... 0.68283797 0.72633956 0.67870546]
 [0.72710453 0.72970378 0.71490319 ... 0.64896781 0.7290976  0.70825632]
 [0.73099834 0.73098715 0.5680931  ... 0.71732139 0.71895887 0.70928193]] [ 0  0  0 ... 29 29 29]


## Prepararing Data for train data 2000

In [ ]:
feature_2000 = df_GAN.to_numpy()
#feature_2000 = sigmoid(feature_2000)
labels_2000 = []
label = 30
for i in range(1, len(feature_2000)+1):
    labels_2000.append(label)
    if (i%200) == 0:
        label += 1
labels_2000 = np.array(labels_2000)
print(feature_2000, labels_2000)

## Prepararing Data for train data 3000

In [ ]:
feature_3000 = GAN['gan_feat']
feature_3000 = sigmoid(feature_3000)
labels_3000 = []
label = 30
for i in range(1, len(feature_3000)+1):
    labels_3000.append(label)
    if (i%300) == 0:
        label += 1
labels_3000 = np.array(labels_3000)
print(feature_3000, labels_3000)

[[0.7310555  0.73105858 0.26911574 ... 0.73105858 0.67686428 0.27557619]
 [0.26895471 0.27263321 0.26894177 ... 0.26910227 0.73089502 0.2690267 ]
 [0.62444266 0.28357538 0.26894142 ... 0.69975452 0.26894142 0.60638138]
 ...
 [0.26933217 0.73104961 0.27997851 ... 0.67667522 0.73084805 0.26894178]
 [0.33651455 0.73105858 0.27924603 ... 0.71915906 0.38880054 0.66023114]
 [0.69294977 0.7310584  0.73105858 ... 0.73102649 0.73105858 0.27523809]] [30 30 30 ... 41 41 41]


## Preparating Data for test 908

In [ ]:
df_test1.drop(df_test1.columns[[0]], axis=1, inplace=True)
label = df_test1['0']
labels_test1 = label.to_numpy()
for i, l in enumerate(labels_test1):
    labels_test1[i] = l + 30
labels_test1 = labels_test1.astype(np.int32)
df_test1.drop(df_test1.columns[[0]], axis=1, inplace=True)
feature_test1 = df_test1.to_numpy()
#feature_test1 = sigmoid(feature_test1)
print(labels_test1, feature_test1)

[30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30
 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30
 30 30 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31
 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31
 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31
 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31 31
 31 31 31 31 31 31 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32
 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32
 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32
 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32 32
 32 32 32 32 32 32 32 32 32 32 33 33 33 33 33 33 33 33 33 33 33 33 33 33
 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33
 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33
 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33 33

## Preparating Data for test 1560

In [ ]:
df_test2.drop(df_test2.columns[[0]], axis=1, inplace=True)
label = df_test2['0']
labels_test2 = label.to_numpy()
labels_test2 = labels_test2.astype(np.int32)
df_test2.drop(df_test2.columns[[0]], axis=1, inplace=True)
feature_test2 = df_test2.to_numpy()
#feature_test2 = sigmoid(feature_test2)
print(feature_test2, labels_test2)

[[9.75723960e-05 6.44414322e-05 2.75831611e-04 ... 6.59246507e-05
  3.88099870e-05 9.59341065e-04]
 [1.68535498e-03 7.38422503e-04 6.74548442e-04 ... 6.16500445e-04
  4.32410423e-04 2.69808806e-03]
 [2.01676972e-03 8.00377922e-04 9.69660119e-04 ... 4.15853079e-04
  5.47979085e-04 2.14829319e-03]
 ...
 [1.09083788e-03 2.63863854e-04 2.65379378e-04 ... 1.13549002e-03
  1.49022217e-03 9.47019202e-04]
 [1.08464749e-03 4.78463480e-04 2.51701043e-04 ... 5.44281735e-04
  1.12532417e-03 5.76747116e-04]
 [9.34650656e-04 5.93126111e-04 3.27518559e-04 ... 3.45751672e-04
  1.34801399e-03 5.12584171e-04]] [ 0  0  0 ... 29 29 29]


## Append two test1 and test2

In [ ]:
feature_test = np.concatenate((feature_test2, feature_test1), axis=0)
labels_test = np.concatenate((labels_test2, labels_test1), axis=0)

In [ ]:
labels_test.shape

(2468,)

# Custom Dataset

In [ ]:
class FeatureData(Dataset):
    def __init__(self, feature, label):
        self.feature = feature
        self.label = label  

    def __len__(self):
        return len(self.feature)

    def __getitem__(self, idx):
        return {'feature': self.feature[idx], 
                'category': self.label[idx]}

In [ ]:
valid_ds1 = FeatureData(feature_test1, labels_test1)
valid_loader1 = DataLoader(dataset=valid_ds1, batch_size=64)

In [ ]:
train_ds1 = FeatureData(feature, labels)
train_ds2 = FeatureData(feature_3000, labels_3000)
#valid_ds = FeatureData(feature_test, labels_test)
train_loader1 = DataLoader(dataset=train_ds1, batch_size=32, shuffle=True)
train_loader2 = DataLoader(dataset=train_ds2, batch_size=64, shuffle=True)
#valid_loader = DataLoader(dataset=valid_ds, batch_size=64)

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
print(device)

cuda:0


# Model with 40 classes

In [ ]:
import torch
import torch.nn as nn
import numpy as np
import torch.nn.functional as F

class PointNet(nn.Module):
    def __init__(self, classes = 40):
        super().__init__()
        self.fc1 = nn.Linear(1024, 512)
        self.fc2 = nn.Linear(512, 256)
        self.fc3 = nn.Linear(256, classes)
        
        self.bn1 = nn.BatchNorm1d(512)
        self.bn2 = nn.BatchNorm1d(256)
        self.dropout = nn.Dropout(p=0.3)
        self.logsoftmax = nn.LogSoftmax(dim=1)

    def forward(self, input):
        xb = input
        xb = F.relu(self.bn1(self.fc1(xb)))
        xb = F.relu(self.bn2(self.dropout(self.fc2(xb))))
        output = self.fc3(xb)
        return self.logsoftmax(output)

# Extracting the parameters and Add some parameters

In [ ]:
PATH = "/content/gdrive/MyDrive/Thesis_work/POINTNET/tanh/tanh_17_83.pth"
checkpoint = torch.load(PATH)
x = checkpoint['model_state_dict']
y = dict(x)
print(y.keys())

dict_keys(['transform.input_transform.conv1.weight', 'transform.input_transform.conv1.bias', 'transform.input_transform.conv2.weight', 'transform.input_transform.conv2.bias', 'transform.input_transform.conv3.weight', 'transform.input_transform.conv3.bias', 'transform.input_transform.fc1.weight', 'transform.input_transform.fc1.bias', 'transform.input_transform.fc2.weight', 'transform.input_transform.fc2.bias', 'transform.input_transform.fc3.weight', 'transform.input_transform.fc3.bias', 'transform.input_transform.bn1.weight', 'transform.input_transform.bn1.bias', 'transform.input_transform.bn1.running_mean', 'transform.input_transform.bn1.running_var', 'transform.input_transform.bn1.num_batches_tracked', 'transform.input_transform.bn2.weight', 'transform.input_transform.bn2.bias', 'transform.input_transform.bn2.running_mean', 'transform.input_transform.bn2.running_var', 'transform.input_transform.bn2.num_batches_tracked', 'transform.input_transform.bn3.weight', 'transform.input_transfor

In [ ]:
z = list(y.keys())
y = []
for i in range(95, 111):
    y.append(z[i])
print(y)
a = dict(x)
new_dict = {}
for n in y:
    new_dict[n] = a[n]
print(len(new_dict))

['fc1.weight', 'fc1.bias', 'fc2.weight', 'fc2.bias', 'fc3.weight', 'fc3.bias', 'bn1.weight', 'bn1.bias', 'bn1.running_mean', 'bn1.running_var', 'bn1.num_batches_tracked', 'bn2.weight', 'bn2.bias', 'bn2.running_mean', 'bn2.running_var', 'bn2.num_batches_tracked']
16


## Add new weight to model 

In [ ]:
rand_tensor = torch.rand((10, 256))
rand = rand_tensor.to('cuda:0')
x = new_dict['fc3.weight']
y = torch.cat((x, rand))
#print(y.size())
new_dict['fc3.weight'] = y

## Add new bias to layer fc3

In [ ]:
rand_tensor = torch.rand(10)
rand = rand_tensor.to('cuda:0')
x = new_dict['fc3.bias']
y = torch.cat((x, rand))
#print(y.size())
new_dict['fc3.bias'] = y

In [ ]:
import collections
model_state_dict = collections.OrderedDict(new_dict)
#print(model_state_dict)

In [ ]:
model = PointNet()
model.to(device)

PointNet(
  (fc1): Linear(in_features=1024, out_features=512, bias=True)
  (fc2): Linear(in_features=512, out_features=256, bias=True)
  (fc3): Linear(in_features=256, out_features=40, bias=True)
  (bn1): BatchNorm1d(512, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (bn2): BatchNorm1d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (dropout): Dropout(p=0.3, inplace=False)
  (logsoftmax): LogSoftmax(dim=1)
)

In [ ]:
model.load_state_dict(model_state_dict)

<All keys matched successfully>

In [ ]:
optimizer = torch.optim.Adam(model.parameters(), lr=0.0001)
criterion = torch.nn.CrossEntropyLoss()
#criterion = torch.nn.NLLLoss()

In [ ]:
from itertools import cycle

def train(model, train_loader1, train_loader2, val_loader=None,  epochs=10, save=True):

    best_acc = 0
    best_epoch = 0

    for epoch in range(epochs): 
        model.train()
        running_loss = 0.0
        for i, data in enumerate(zip(cycle(train_loader2), train_loader1)):
        # for i, data in enumerate(train_loader1, 0):
        #     inputs, labels = data['feature'].to(device).float(), data['category'].to(device).long()
        #     print(data[0]['category'].size())
        #     print(data[1]['category'].size())
            
        #     print(p.size())
            
        #     print(p)
        
            feature = torch.cat((data[0]['feature'], data[1]['feature']))
            label = torch.cat((data[0]['category'], data[1]['category']))
            perm = torch.randperm(feature.size()[0])
            feature = feature[perm]
            label = label[perm]
            inputs, labels = feature.to(device).float(), label.to(device)
            optimizer.zero_grad()
            outputs = model(inputs)
            #print(outputs)
            loss = criterion(outputs, labels)
            loss.backward()
            optimizer.step()

            # print statistics
            running_loss += loss.item()
            if i % 10 == 9:    # print every 10 mini-batches
                    print('[Epoch: %d, Batch: %4d / %4d], loss: %.3f' %
                        (epoch + 1, i + 1, len(train_loader1), running_loss / 10))
                    running_loss = 0.0
        #print(outputs, labels)
        model.eval()
        correct = total = 0

        # save the model
        if save:
          torch.save({
            'epoch': epoch,
            'model_state_dict': model.state_dict(),
            'optimizer_state_dict': optimizer.state_dict(),
            'loss': loss,
            }, "GAN"+str(epoch)+".pth")
          
        # validation
        if val_loader:
            with torch.no_grad():
                for data in val_loader:
                    inputs, labels = data['feature'].to(device).float(), data['category'].to(device)
                    outputs = model(inputs)
                    _, predicted = torch.max(outputs.data, 1)
                    total += labels.size(0)
                    correct += (predicted == labels).sum().item()
                val_acc = 100. * correct / total
                if val_acc > best_acc:
                    best_acc = val_acc
                    best_epoch = epoch
        print('Valid accuracy: %d %%' % val_acc)
    return best_acc, best_epoch

          #torch.save(pointnet.state_dict(), "save_"+str(epoch)+".pth")

In [ ]:
train(model, train_loader1, train_loader2, valid_loader1, epochs=100, save=False) 

RuntimeError: ignored

# Creating Table

In [ ]:
pip install texttable

In [ ]:
from texttable import Texttable

table = Texttable()

# texttable takes the first reocrd in the list as the column names
# of the table
l = [['GAN(3000)', 'Train(5852)', 'Test908', 'Test1560', 'Valid Accuracy'], 
         [u'\u2718', u'\u2718', u'\u2718', u'\u2718', '53.08%'], 
         [u'\u2714', u'\u2718', u'\u2718', u'\u2718', '52.96%'], 
         [u'\u2714', u'\u2718', u'\u2714', u'\u2718', '57.13%%'], 
         [u'\u2714', u'\u2714', u'\u2714', u'\u2714', '52.31%']
        ]

#table.set_deco(Texttable.HEADER)
# table.set_cols_dtype(['t',  # Symbol
#                         't',  # Symbol
#                         't',  # Symbol
#                         't',  # Symbol
#                         'i']) # Integer
table.set_cols_align(["c", "c", "c", "c", "c"])
table.add_rows(l)
print(f"\n\nSeen Feature(5852) vs Seen Test(1560) accuracy is 85%\n\n\u2718 = Not Normalized\n\u2714 = Normalized")
print (table.draw())



Seen Feature(5852) vs Seen Test(1560) accuracy is 85%

✘ = Not Normalized
✔ = Normalized
+-----------+-------------+---------+----------+----------------+
| GAN(3000) | Train(5852) | Test908 | Test1560 | Valid Accuracy |
+===========+=============+=========+==========+================+
|     ✘     |      ✘      |    ✘    |    ✘     |     53.08%     |
+-----------+-------------+---------+----------+----------------+
|     ✔     |      ✘      |    ✘    |    ✘     |     52.96%     |
+-----------+-------------+---------+----------+----------------+
|     ✔     |      ✘      |    ✔    |    ✘     |    57.13%%     |
+-----------+-------------+---------+----------+----------------+
|     ✔     |      ✔      |    ✔    |    ✔     |     52.31%     |
+-----------+-------------+---------+----------+----------------+


In [ ]:
from texttable import Texttable

table = Texttable()

# texttable takes the first reocrd in the list as the column names
# of the table
l = [['GAN(3000)', 'Train(5852)', 'Test908', 'Test1560', 'Valid Accuracy'], 
         [u'\u2718', u'\u2718', u'\u2718', u'\u2718', '50%'], 
         [u'\u2714', u'\u2718', u'\u2718', u'\u2718', '52%'], 
         [u'\u2714', u'\u2718', u'\u2714', u'\u2718', '55%%'], 
         [u'\u2714', u'\u2714', u'\u2714', u'\u2714', '51%']
        ]

#table.set_deco(Texttable.HEADER)
# table.set_cols_dtype(['t',  # Symbol
#                         't',  # Symbol
#                         't',  # Symbol
#                         't',  # Symbol
#                         'i']) # Integer
table.set_cols_align(["c", "c", "c", "c", "c"])
table.add_rows(l)
print(f"\n\nSeen Feature(5852) vs Seen Test(1560) accuracy is 85%\n\n\u2718 = Not Normalized\n\u2714 = Normalized")
print (table.draw())



Seen Feature(5852) vs Seen Test(1560) accuracy is 85%

✘ = Not Normalized
✔ = Normalized
+-----------+-------------+---------+----------+----------------+
| GAN(3000) | Train(5852) | Test908 | Test1560 | Valid Accuracy |
+===========+=============+=========+==========+================+
|     ✘     |      ✘      |    ✘    |    ✘     |      50%       |
+-----------+-------------+---------+----------+----------------+
|     ✔     |      ✘      |    ✘    |    ✘     |      52%       |
+-----------+-------------+---------+----------+----------------+
|     ✔     |      ✘      |    ✔    |    ✘     |      55%%      |
+-----------+-------------+---------+----------+----------------+
|     ✔     |      ✔      |    ✔    |    ✔     |      51%       |
+-----------+-------------+---------+----------+----------------+


# New Loss Function

## Model

In [ ]:
optimizer = torch.optim.Adam(model.parameters(), lr=0.0001)
def avg_loss(y_test1, y_label1, y_test2, y_label2, alpha):
  loss = nn.CrossEntropyLoss()
  return alpha * loss(y_test1, y_label1) + (1 - alpha) * loss(y_test2, y_label2)

In [ ]:
def divide(output, ind):
    return output[:ind], output[ind:len(output)]

In [ ]:
from itertools import cycle

def train1(model, train_loader1, train_loader2, val_loader=None,  epochs=10, save=True):
    best_acc = 0
    best_epoch = 0
    for epoch in range(epochs): 
        model.train()
        running_loss = 0.0
        for i, data in enumerate(zip(cycle(train_loader2), train_loader1)):
            #ind = torch.cat((torch.zeros(len(data[0]['feature'])), torch.ones(len(data[1]['feature']))))
            feature = torch.cat((data[0]['feature'], data[1]['feature']))
            label = torch.cat((data[0]['category'], data[1]['category']))
            # perm = torch.randperm(feature.size()[0])
            # feature = feature[perm]
            # label = label[perm]
            # ind = ind[perm]
            inputs, labels = feature.to(device).float(), label.to(device)
            optimizer.zero_grad()
            outputs = model(inputs)
            #print(len(outputs))
            output1, output2 = divide(outputs, len(data[0]['feature']))
            loss = avg_loss(output1, data[0]['category'].to(device).long(), output2, data[1]['category'].to(device).long(), .7)
            loss.backward()
            optimizer.step()

            # print statistics
            running_loss += loss.item()
            if i % 10 == 9:    # print every 10 mini-batches
                    print('[Epoch: %d, Batch: %4d / %4d], loss: %.3f' %
                        (epoch + 1, i + 1, len(train_loader1), running_loss / 10))
                    running_loss = 0.0
        #print(outputs, labels)
        model.eval()
        correct = total = 0

        # save the model
        if save:
          torch.save({
            'epoch': epoch,
            'model_state_dict': model.state_dict(),
            'optimizer_state_dict': optimizer.state_dict(),
            'loss': loss,
            }, "GAN"+str(epoch)+".pth")
          
        # validation
        if val_loader:
            with torch.no_grad():
                for data in val_loader:
                    inputs, labels = data['feature'].to(device).float(), data['category'].to(device)
                    outputs = model(inputs)
                    _, predicted = torch.max(outputs.data, 1)
                    total += labels.size(0)
                    correct += (predicted == labels).sum().item()
            val_acc = 100. * correct / total
            if val_acc > best_acc:
                best_acc = val_acc
                best_epoch = epoch
            print('Valid accuracy: %d %%' % val_acc)
    return best_acc, best_epoch

          #torch.save(pointnet.state_dict(), "save_"+str(epoch)+".pth")

In [ ]:
acc, epoch = train1(model, train_loader1, train_loader2, valid_loader1, epochs=300, save=False) 

Streaming output truncated to the last 5000 lines.
[Epoch: 37, Batch:  170 /  183], loss: 2.698
[Epoch: 37, Batch:  180 /  183], loss: 2.769
Valid accuracy: 0 %
[Epoch: 38, Batch:   10 /  183], loss: 2.747
[Epoch: 38, Batch:   20 /  183], loss: 2.705
[Epoch: 38, Batch:   30 /  183], loss: 2.805
[Epoch: 38, Batch:   40 /  183], loss: 2.721
[Epoch: 38, Batch:   50 /  183], loss: 2.719
[Epoch: 38, Batch:   60 /  183], loss: 2.796
[Epoch: 38, Batch:   70 /  183], loss: 2.730
[Epoch: 38, Batch:   80 /  183], loss: 2.785
[Epoch: 38, Batch:   90 /  183], loss: 2.768
[Epoch: 38, Batch:  100 /  183], loss: 2.702
[Epoch: 38, Batch:  110 /  183], loss: 2.703
[Epoch: 38, Batch:  120 /  183], loss: 2.747
[Epoch: 38, Batch:  130 /  183], loss: 2.746
[Epoch: 38, Batch:  140 /  183], loss: 2.746
[Epoch: 38, Batch:  150 /  183], loss: 2.708
[Epoch: 38, Batch:  160 /  183], loss: 2.709
[Epoch: 38, Batch:  170 /  183], loss: 2.733
[Epoch: 38, Batch:  180 /  183], loss: 2.785
Valid accuracy: 0 %
[Epoch: 3

In [ ]:
print(f"Best Accuracy at epoch {epoch}, Accuracy {acc:.2f}%")

Best Accuracy at epoch 0, Accuracy 17.29%


In [ ]:
/content/gdrive/MyDrive/Thesis_work/POINTNET/csv_tanh/feature_vector_train_model30.csv

In [ ]:
import pickle

with open('/content/gdrive/MyDrive/Thesis_work/zhu_ZSL_GAN/ZSL_GAN/data/ModelNet40/train_label.pkl', 'rb') as f:
    data = pickle.load(f)

In [ ]:
data

array([ 0,  0,  0, ..., 29, 29, 29])

In [ ]:
import pandas as pd
df_train = pd.read_csv('/content/gdrive/MyDrive/Thesis_work/POINTNET/csv_tanh/feature_vector_train_model30.csv')
df_train.drop(df_train.columns[[0]], axis=1, inplace=True)

In [ ]:
label = df_train.iloc[:, 0]

In [ ]:
label = label.to_numpy()

In [ ]:
label = label.astype(int)

In [ ]:
label

array([ 0,  0,  0, ..., 29, 29, 29])

In [ ]:
(data==label).all()

True